<a href="https://colab.research.google.com/github/josher19/solar-notebook/blob/main/satellite_and_weather.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Segment Anything Model for Geospatial Data

[![image](https://studiolab.sagemaker.aws/studiolab.svg)](https://studiolab.sagemaker.aws/import/github/josher19/solar-notebook/blob/main/satellite_and_weather.ipynb)
[![image](https://img.shields.io/badge/Open-Planetary%20Computer-black?style=flat&logo=microsoft)](https://pccompute.westeurope.cloudapp.azure.com/compute/hub/user-redirect/git-pull?repo=https://github.com/josher19/solar-notebook/blob/main/satellite_and_weather.ipynb&branch=main)
[![image](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/josher19/solar-notebook/blob/main/satellite_and_weather.ipynb)

This notebook shows how to use segment satellite imagery using the Segment Anything Model (SAM) with a few lines of code.

Make sure you use GPU runtime for this notebook. For Google Colab, go to `Runtime` -> `Change runtime type` and select `GPU` as the hardware accelerator.

## Install dependencies

Uncomment and run the following cell to install the required dependencies.


In [ ]:
%pip install segment-geospatial

## Import libraries

In [10]:
import os
import leafmap
from samgeo import SamGeo, tms_to_geotiff, get_basemaps

In [108]:
from geopy.geocoders import Nominatim

geolocator = Nominatim(user_agent="myApp")
address = "2050 NE Mays Ave, Bend, OR 97701" # House with Solar Panels
location = geolocator.geocode(address)
map_location = [location.latitude, location.longitude]
print('Lat-Lon:', map_location, "in", ", ".join(address.split(", ")[-2:]))

Lat-Lon: [44.08284601446541, -121.27319196509396] in Bend, OR 97701


## Create an interactive map

In [120]:
# m = leafmap.Map(center=[29.676840, -95.369222], zoom=19)
m = leafmap.Map(center=map_location, zoom=20)
m.add_basemap("SATELLITE")
m

Map(center=[44.08284601446541, -121.27319196509396], controls=(ZoomControl(options=['position', 'zoom_in_text'…

In [116]:
bbox = m.get_bbox() or [-121.27408638596536,
 44.08256802919778,
 -121.27296119928361,
 44.083146046165986]

Pan and zoom the map to select the area of interest. Use the draw tools to draw a polygon or rectangle on the map

In [45]:
# if m.user_roi_bounds() is not None:
#    bbox = m.user_roi_bounds()
# else:
#    bbox = [-95.3704, 29.6762, -95.368, 29.6775]

## Download map tiles

Download maps tiles and mosaic them into a single GeoTIFF file

In [117]:
image = "satellite.tif"

Besides the `satellite` basemap, you can use any of the following basemaps returned by the `get_basemaps()` function:

In [ ]:
# get_basemaps().keys()

Specify the basemap as the source.

In [121]:
tms_to_geotiff(output=image, bbox=bbox, zoom=21, source="Satellite", overwrite=True)

Downloaded image 01/55
Downloaded image 02/55
Downloaded image 03/55
Downloaded image 04/55
Downloaded image 05/55
Downloaded image 06/55
Downloaded image 07/55
Downloaded image 08/55
Downloaded image 09/55
Downloaded image 10/55
Downloaded image 11/55
Downloaded image 12/55
Downloaded image 13/55
Downloaded image 14/55
Downloaded image 15/55
Downloaded image 16/55
Downloaded image 17/55
Downloaded image 18/55
Downloaded image 19/55
Downloaded image 20/55
Downloaded image 21/55
Downloaded image 22/55
Downloaded image 23/55
Downloaded image 24/55
Downloaded image 25/55
Downloaded image 26/55
Downloaded image 27/55
Downloaded image 28/55
Downloaded image 29/55
Downloaded image 30/55
Downloaded image 31/55
Downloaded image 32/55
Downloaded image 33/55
Downloaded image 34/55
Downloaded image 35/55
Downloaded image 36/55
Downloaded image 37/55
Downloaded image 38/55
Downloaded image 39/55
Downloaded image 40/55
Downloaded image 41/55
Downloaded image 42/55
Downloaded image 43/55
Downloaded 

You can also use your own image. Uncomment and run the following cell to use your own image.

In [28]:
# image = '/path/to/your/own/image.tif'

Display the downloaded image on the map.

In [122]:
m.layers[-1].visible = False  # turn off the basemap
m.add_raster(image, layer_name="Image")
m

Map(bottom=97522787.0, center=[44.08284601446541, -121.27319196509396], controls=(ZoomControl(options=['positi…

![](https://i.imgur.com/KAm84IY.png)

## Initialize SAM class

In [30]:
sam = SamGeo(
    model_type="vit_h",
    checkpoint="sam_vit_h_4b8939.pth",
    sam_kwargs=None,
)

Model checkpoint for vit_h not found.


Downloading...
From: https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth
To: /root/.cache/torch/hub/checkpoints/sam_vit_h_4b8939.pth
100%|██████████| 2.56G/2.56G [00:23<00:00, 109MB/s]


## Segment the image

Set `batch=True` to segment the image in batches. This is useful for large images that cannot fit in memory.

In [31]:
mask = "segment.tif"
sam.generate(
    image, mask, batch=True, foreground=True, erosion_kernel=(3, 3), mask_multiplier=255
)

100%|██████████| 4/4 [00:32<00:00,  8.00s/it]


## Polygonize the raster data

Save the segmentation results as a GeoPackage file.

In [32]:
vector = "segment.gpkg"
sam.tiff_to_gpkg(mask, vector, simplify_tolerance=None)

You can also save the segmentation results as any vector data format supported by GeoPandas.

In [33]:
shapefile = "segment.shp"
sam.tiff_to_vector(mask, shapefile)

## Visualize the results

In [125]:
style = {
    "color": "#3388ff",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0.5,
}
m.add_vector(vector, layer_name="Vector", style=style, zoom_to_layer=True)
m

Map(bottom=48761538.0, center=[44.08285703838782, -121.27352446317674], controls=(ZoomControl(options=['positi…

![](https://i.imgur.com/Ysq3u7E.png)

In [71]:
%pip install python-weather emoji

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 457.9/457.9 kB 6.2 MB/s eta 0:00:00


In [102]:
# import the module
import python_weather
import emoji

import asyncio
import os

async def getweather():
  # declare the client. the measuring unit used defaults to the metric system (celcius, km/h, etc.)
  async with python_weather.Client(unit=python_weather.IMPERIAL) as client:
    # fetch a weather forecast from a city
    weather = await client.get('Bend, OR')

    # returns the current day's forecast temperature (int)
    print(f"Current Temperature: {weather.current.temperature}°F\n")

    # get the weather forecast
    for forecast in weather.forecasts:
      # print the date and the average temperature
      # print(f"{forecast.date.strftime('%a')} {forecast.date}: average of {forecast.temperature}°F", forecast)
      print(f"{forecast.date.strftime('%a')} {forecast.date}: Sunrise: {forecast.astronomy.sun_rise.strftime('%H:%M')} {emoji.emojize(':sunrise:')} | Sunset: {forecast.astronomy.sun_set.strftime('%H:%M')} {emoji.emojize(':sunset:')} | average of {forecast.temperature}°F {emoji.emojize(':thermometer:')}")

      # hourly forecasts
      for hourly in forecast.hourly:
        # print the hour, temperature, and description
        print(f' --> {hourly.time.hour}:00: {hourly.temperature}°F, {hourly.description}')




if __name__ == '__main__':
  # see https://stackoverflow.com/questions/45600579/asyncio-event-loop-is-closed-when-getting-loop
  # for more details
  if os.name == 'nt':
    asyncio.set_event_loop_policy(asyncio.WindowsSelectorEventLoopPolicy())

  # asyncio.run(getweather())
  await getweather()

Current Temperature: 27°F

Thu 2024-01-18: Sunrise: 07:36 🌅 | Sunset: 16:56 🌇 | average of 31°F 🌡️
 --> 0:00: 36°F, Patchy rain possible
 --> 3:00: 36°F, Fog
 --> 6:00: 36°F, Moderate snow
 --> 9:00: 34°F, Light snow
 --> 12:00: 33°F, Light sleet
 --> 15:00: 30°F, Heavy snow
 --> 18:00: 24°F, Moderate or heavy freezing rain
 --> 21:00: 23°F, Light snow
Fri 2024-01-19: Sunrise: 07:35 🌅 | Sunset: 16:58 🌇 | average of 26°F 🌡️
 --> 0:00: 24°F, Freezing fog
 --> 3:00: 25°F, Freezing fog
 --> 6:00: 25°F, Freezing fog
 --> 9:00: 24°F, Freezing fog
 --> 12:00: 26°F, Freezing fog
 --> 15:00: 28°F, Freezing fog
 --> 18:00: 26°F, Freezing fog
 --> 21:00: 26°F, Freezing fog
Sat 2024-01-20: Sunrise: 07:34 🌅 | Sunset: 16:59 🌇 | average of 31°F 🌡️
 --> 0:00: 29°F, Freezing fog
 --> 3:00: 28°F, Mist
 --> 6:00: 28°F, Mist
 --> 9:00: 29°F, Mist
 --> 12:00: 32°F, Fog
 --> 15:00: 34°F, Light sleet
 --> 18:00: 33°F, Mist
 --> 21:00: 35°F, Fog
